# Setup UI

In [9]:
import os
import json

# If the file does not exist it'll default to the manual setting see below
filePathToSettingsFile = '../../env/ai.json'

# Is there a settings file? 
if os.path.exists(filePathToSettingsFile):
    # Yes there is so load settings from there
    
    print(f'Loading settings from {filePathToSettingsFile}')
    f = open(filePathToSettingsFile)
    settingsJson = json.load(f)
    del f

    for key in settingsJson:
        os.environ[key] = settingsJson[key]
        
    del settingsJson
else:        
    # Set variables manually
    
    print('Setting variables manually as there is not ai.json settings file')

    # Update the variables below with your own settings
    os.environ['REQUESTS_CA_BUNDLE'] = '../../env/ZCert.pem'    
    os.environ['HUGGING_FACE_API_KEY'] = 'Get here: https://huggingface.co/settings/tokens'
    os.environ['OPENAI_API_KEY'] = 'Get here: https://platform.openai.com/account/api-keys'
    os.environ["SERPAPI_API_KEY"] = 'serpapi KEY, Get here: https://serpapi.com/manage-api-key'    

Loading settings from ../../env/ai.json


In [10]:
import os
import pinecone
from langchain.chains import RetrievalQA
from langchain.embeddings import OpenAIEmbeddings
from langchain.llms import OpenAI
from langchain.vectorstores import Pinecone
import gradio as gr

# Setup Vector Store
There are two vector stores in Pinecone (hence the two API Keys). Each has a separate knowledge base
1. Roman history
2. A list of literature

In [65]:
embeddings = OpenAIEmbeddings()

vector_store = None

def create_vector_store(indexToUse: str):
    
    if indexToUse == "Roman History":
        print(f"Using vector store: {indexToUse}")
        apiKeyKey = "PINECONE_API_KEY_2"
        apiEnvKey = "PINECONE_API_ENV_2"
        testQuestion = "When was Ceasar born?"
    else:
        print(f"Using vector store: {indexToUse}")
        apiKeyKey = "PINECONE_API_KEY"
        apiEnvKey = "PINECONE_API_ENV"
        testQuestion = "What is Moby Dick?"
        
    pinecone.init(api_key=os.environ[apiKeyKey], environment=os.environ[apiEnvKey])

    index_name = pinecone.list_indexes()[0]
    print(f"Using index: {index_name}")
    index = pinecone.Index(index_name)
    vector_store = Pinecone(index, embeddings, "text")    

    # query = testQuestion
    # print(f'Test questions: {testQuestion}')
    # result = vector_store.similarity_search(query, k=3)
    # print(result[0])
    
    return vector_store

vector_store = create_vector_store("Roman History")

Using vector store: Roman History
Using index: rag-demo-1-history-rome


In [66]:
llm = OpenAI(temperature=0)

# Conversational agent

In [67]:
from langchain.memory import ConversationBufferMemory
from langchain.chains import ConversationalRetrievalChain

memory = ConversationBufferMemory(memory_key="chat_history", return_messages= True)
chain = ConversationalRetrievalChain.from_llm(llm, retriever= vector_store.as_retriever(), memory= memory)

In [68]:
query = """ 
    SYSTEM:
    You are a helpful teacher who is teaching a class of 10 year olds. 
    Your answers must only come from the context provided to you in the question.
    If you don't know the answer then say so. 
    The answers should be at least 40 words or longer
    
    QUESTION:
    Why was he avenging Crassus, what happened to him that Ceasar needed to avenge him? 
    
"""
chain.run({'question': query})

' \nCrassus was a Roman general who was killed in battle by the Parthians. He was killed while trying to extend the Roman Empire into the Middle East. Ceasar was avenging Crassus by trying to defeat the Parthians and expand the Roman Empire. He was also trying to avenge the death of his friend and mentor.'

# UI
1. https://medium.com/@gabriel_renno/how-to-build-a-gpt3-5-powered-chatbot-for-your-landing-page-with-langchain-and-gradio-1236ddfb0cf1
2. https://github.com/RajKKapadia/YouTube-Pinecone-Demo

In [109]:
# RajKKapadi's 
from langchain.chains import ConversationalRetrievalChain
from langchain.chat_models import ChatOpenAI
from langchain.vectorstores import Pinecone
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.memory import ConversationBufferMemory
import pinecone

def create_conversation(query: str, chat_history: list, indexToUse: str) -> tuple: 
    try:
        #vector_store = create_vector_store("Roman History")
        print(indexToUse)
        vector_store = create_vector_store("Literature")
        memory = ConversationBufferMemory(
            memory_key='chat_history',
            return_messages=False
        )
        cqa = ConversationalRetrievalChain.from_llm(
            llm=ChatOpenAI(temperature=0.0,
                           openai_api_key=os.environ['OPENAI_API_KEY']),
            retriever=vector_store.as_retriever(search_kwargs={"k": 5}),
            memory=memory,
            get_chat_history=lambda h: h,
        )
        result = cqa({'question': query, 'chat_history': chat_history})
        chat_history.append((query, result['answer']))
        return '', chat_history, indexToUse
    except Exception as e:
        chat_history.append((query, e))
        return '', chat_history

In [113]:


# vector_store_index_to_use = None 
# def set_vector_store_index(indexName:str):
#     vector_store_index_to_use = indexName
    
# with gr.Blocks() as demo:
#     indexToUseDD = gr.Dropdown(choices=["Roman History", "Literature"])

In [114]:
import gradio as gr

with gr.Blocks() as demo:
    gr.Markdown("Chat to docs")
    indexToUseDD = gr.Dropdown(choices=["Roman History", "Literature"])
    chatbot = gr.Chatbot(label='Talk to the Doument')
    msg = gr.Textbox()
    
    submitBtn = gr.Button(value="Submit")    
    clear = gr.ClearButton([msg, chatbot])

    msg.submit(create_conversation, [msg, chatbot, indexToUseDD], [msg, chatbot, indexToUseDD])
    submitBtn.click(create_conversation, [msg, chatbot, indexToUseDD], [msg, chatbot, indexToUseDD])

if __name__ == '__main__':
    demo.launch(show_error=True) #show_error=True, debug=True)

Running on local URL:  http://127.0.0.1:7918

To create a public link, set `share=True` in `launch()`.


Literature
Using vector store: Literature
Using index: rag-demo-1-literature
Literature
Using vector store: Literature
Using index: rag-demo-1-literature
Literature
Using vector store: Literature
Using index: rag-demo-1-literature
Literature
Using vector store: Literature
Using index: rag-demo-1-literature
Literature
Using vector store: Literature
Using index: rag-demo-1-literature
Literature
Using vector store: Literature
Using index: rag-demo-1-literature
Literature
Using vector store: Literature
Using index: rag-demo-1-literature
